# Linesearch methods

Consider $f \in C^2$.  A descent method consists to iteratively compute
$$
x_{k+1} = x_k + \alpha^* d_k
$$
where $\alpha^*$ approximately minimizes $f(x_k - \alpha d_k)$.

In [1]:
using Optim
using Plots
plotly()

┌ Info: Precompiling Optim [429524aa-4258-5aef-a3af-852621145aeb]
└ @ Base loading.jl:1273
  ** incremental compilation may be fatally broken for this module **

┌ Info: For saving to png with the Plotly backend ORCA has to be installed.
└ @ Plots C:\Users\slash\.julia\packages\Plots\qZHsp\src\backends.jl:363


Plots.PlotlyBackend()

Several linesearch techniques are proposed in Julia, as explained in the page https://github.com/JuliaNLSolvers/LineSearches.jl

Consider again the Rosenbrock example, whose mathematical expression is

$$
f(x,y) = (1-x)^2 + 100(y-x^2)^2
$$

Its gradient can be computed as

$$
\nabla f(x,y) =
\begin{pmatrix}
-2(1-x)-400x(y-x^2) \\
200(y-x^2)
\end{pmatrix}
$$

$$
\nabla^2 f(x,y) =
\begin{pmatrix}
2 - 400(y-x^2) + 800x^2 & -400x \\
-400x & 200
\end{pmatrix}
=
\begin{pmatrix}
2 - 400y + 1200x^2 & -400x \\
-400x & 200
\end{pmatrix}
$$

The minimizer is located at $(1,1)$. Indeed,
$$
\nabla f(1,1) = \begin{pmatrix} 0 \\ 0 \end{pmatrix}
$$
and
$$
\nabla^2 f(1,1) =
\begin{pmatrix}
802 & -400 \\ -400 & 200
\end{pmatrix}
$$
The determinants of the principal minors are positive as they are respectively 802 and $802\times200-400^2= 400$, so the Hessian is positive definite.

In [3]:
# Rosenbrock function
# Source: https://bitbucket.org/lurk3r/optim.jl

function rosenbrock(x::Vector)
    return (1.0 - x[1])^2 + 100.0 * (x[2] - x[1]^2)^2
end

function rosenbrock_gradient!(storage::Vector, x::Vector)
    storage[1] = -2.0 * (1.0 - x[1]) - 400.0 * (x[2] - x[1]^2) * x[1]
    storage[2] = 200.0 * (x[2] - x[1]^2)
end

function rosenbrock_hessian!(storage::Matrix, x::Vector)
    storage[1, 1] = 2.0 - 400.0 * x[2] + 1200.0 * x[1]^2
    storage[1, 2] = -400.0 * x[1]
    storage[2, 1] = -400.0 * x[1]
    storage[2, 2] = 200.0
end

rosenbrock_hessian! (generic function with 1 method)

In [4]:
using Plots

default(size=(600,600), fc=:heat)
x, y = 0:0.02:1.0, 0:0.02:1.0
z = Surface((x,y)->rosenbrock([x,y]), x, y)
surface(x,y,z, linealpha = 0.3)

<!DOCTYPE html>
 
 
 Plots.jl

In [5]:
Plots.contour(x,y,z, linealpha = 0.1, levels=1600)

<!DOCTYPE html>
 
 
 Plots.jl

We can optimize it using the optimize function present in the package optim.jl

In [8]:
res = optimize(rosenbrock, rosenbrock_gradient!,
               [20.0, 20.0],
               Optim.GradientDescent(),
               Optim.Options(g_tol = 1e-6,
                             store_trace = true,
                             show_trace = true))

Iter     Function value   Gradient norm 
     0     1.444036e+07     3.040038e+06
 * time: 0.0
     1     2.680958e+06     8.881503e+05
 * time: 0.003000020980834961
     2     6.986401e+02     4.430920e+03
 * time: 0.006999969482421875
     3     1.422712e+01     2.423975e+02
 * time: 0.020999908447265625
     4     1.241984e+01     7.750435e-01
 * time: 0.03600001335144043
     5     1.241547e+01     1.200614e+01
 * time: 0.0409998893737793
     6     1.241110e+01     8.544267e-01
 * time: 0.04399991035461426
     7     1.241103e+01     8.557174e-01
 * time: 0.056999921798706055
     8     1.241096e+01     8.544292e-01
 * time: 0.06999993324279785
     9     1.241089e+01     8.557152e-01
 * time: 0.09500002861022949
    10     1.241081e+01     8.544285e-01
 * time: 0.12899994850158691
    11     1.241074e+01     8.557130e-01
 * time: 0.16000008583068848
    12     1.241067e+01     8.544278e-01
 * time: 0.18799996376037598
    13     1.241060e+01     8.557108e-01
 * time: 0.2030000686

   119     1.240293e+01     8.555956e-01
 * time: 1.7609999179840088
   120     1.240285e+01     8.543922e-01
 * time: 1.7769999504089355
   121     1.240278e+01     8.555934e-01
 * time: 1.7969999313354492
   122     1.240271e+01     8.543915e-01
 * time: 1.8029999732971191
   123     1.240264e+01     8.555912e-01
 * time: 1.816999912261963
   124     1.240256e+01     8.543909e-01
 * time: 1.8299999237060547
   125     1.240249e+01     8.555891e-01
 * time: 1.8589999675750732
   126     1.240242e+01     8.543902e-01
 * time: 1.877000093460083
   127     1.240235e+01     8.555869e-01
 * time: 1.8970000743865967
   128     1.240227e+01     8.543896e-01
 * time: 1.9259998798370361
   129     1.240220e+01     8.555848e-01
 * time: 1.9300000667572021
   130     1.240213e+01     8.543889e-01
 * time: 1.9719998836517334
   131     1.240206e+01     8.555826e-01
 * time: 2.007999897003174
   132     1.240198e+01     8.543882e-01
 * time: 2.0230000019073486
   133     1.240191e+01     8.555805e

 * time: 3.697000026702881
   239     1.239424e+01     8.554674e-01
 * time: 3.7230000495910645
   240     1.239416e+01     8.543523e-01
 * time: 3.739000082015991
   241     1.239409e+01     8.554653e-01
 * time: 3.746000051498413
   242     1.239402e+01     8.543516e-01
 * time: 3.759000062942505
   243     1.239395e+01     8.554632e-01
 * time: 3.7850000858306885
   244     1.239387e+01     8.543510e-01
 * time: 3.8289999961853027
   245     1.239380e+01     8.554611e-01
 * time: 3.8320000171661377
   246     1.239373e+01     8.543503e-01
 * time: 3.8559999465942383
   247     1.239366e+01     8.554589e-01
 * time: 3.8980000019073486
   248     1.239359e+01     8.543496e-01
 * time: 3.9049999713897705
   249     1.239351e+01     8.554568e-01
 * time: 3.933000087738037
   250     1.239344e+01     8.543490e-01
 * time: 3.953000068664551
   251     1.239337e+01     8.554547e-01
 * time: 3.9560000896453857
   252     1.239330e+01     8.543483e-01
 * time: 3.9779999256134033
   253     1

   360     1.238547e+01     8.543121e-01
 * time: 6.186000108718872
   361     1.238540e+01     8.553395e-01
 * time: 6.20199990272522
   362     1.238533e+01     8.543114e-01
 * time: 6.229000091552734
   363     1.238526e+01     8.553375e-01
 * time: 6.260999917984009
   364     1.238518e+01     8.543107e-01
 * time: 6.2790000438690186
   365     1.238511e+01     8.553354e-01
 * time: 6.299000024795532
   366     1.238504e+01     8.543100e-01
 * time: 6.309000015258789
   367     1.238497e+01     8.553333e-01
 * time: 6.400000095367432
   368     1.238489e+01     8.543094e-01
 * time: 6.414999961853027
   369     1.238482e+01     8.553312e-01
 * time: 6.427999973297119
   370     1.238475e+01     8.543087e-01
 * time: 6.434999942779541
   371     1.238468e+01     8.553292e-01
 * time: 6.448999881744385
   372     1.238460e+01     8.543080e-01
 * time: 6.456000089645386
   373     1.238453e+01     8.553271e-01
 * time: 6.4709999561309814
   374     1.238446e+01     8.543073e-01
 * tim

   482     1.237663e+01     8.542708e-01
 * time: 9.300999879837036
   483     1.237656e+01     8.552140e-01
 * time: 9.32699990272522
   484     1.237649e+01     8.542701e-01
 * time: 9.369999885559082
   485     1.237641e+01     8.552120e-01
 * time: 9.394000053405762
   486     1.237634e+01     8.542695e-01
 * time: 9.42300009727478
   487     1.237627e+01     8.552100e-01
 * time: 9.431999921798706
   488     1.237620e+01     8.542688e-01
 * time: 9.469000101089478
   489     1.237613e+01     8.552079e-01
 * time: 9.4760000705719
   490     1.237605e+01     8.542681e-01
 * time: 9.48799991607666
   491     1.237598e+01     8.552059e-01
 * time: 9.51799988746643
   492     1.237591e+01     8.542674e-01
 * time: 9.53600001335144
   493     1.237584e+01     8.552039e-01
 * time: 9.57800006866455
   494     1.237576e+01     8.542667e-01
 * time: 9.588000059127808
   495     1.237569e+01     8.552018e-01
 * time: 9.611999988555908
   496     1.237562e+01     8.542661e-01
 * time: 9.6310

   602     1.236793e+01     8.542299e-01
 * time: 11.57699990272522
   603     1.236786e+01     8.550929e-01
 * time: 11.592000007629395
   604     1.236779e+01     8.542293e-01
 * time: 11.605999946594238
   605     1.236772e+01     8.550909e-01
 * time: 11.617000102996826
   606     1.236764e+01     8.542286e-01
 * time: 11.644999980926514
   607     1.236757e+01     8.550889e-01
 * time: 11.664999961853027
   608     1.236750e+01     8.542279e-01
 * time: 11.67199993133545
   609     1.236743e+01     8.550869e-01
 * time: 11.677000045776367
   610     1.236735e+01     8.542272e-01
 * time: 11.681999921798706
   611     1.236728e+01     8.550849e-01
 * time: 11.686000108718872
   612     1.236721e+01     8.542265e-01
 * time: 11.70799994468689
   613     1.236714e+01     8.550829e-01
 * time: 11.746000051498413
   614     1.236706e+01     8.542258e-01
 * time: 11.753000020980835
   615     1.236699e+01     8.550809e-01
 * time: 11.759999990463257
   616     1.236692e+01     8.542252e

   722     1.235923e+01     8.541888e-01
 * time: 14.022000074386597
   723     1.235916e+01     8.549738e-01
 * time: 14.050999879837036
   724     1.235909e+01     8.541881e-01
 * time: 14.081000089645386
   725     1.235901e+01     8.549719e-01
 * time: 14.098000049591064
   726     1.235894e+01     8.541874e-01
 * time: 14.105999946594238
   727     1.235887e+01     8.549699e-01
 * time: 14.114000082015991
   728     1.235880e+01     8.541867e-01
 * time: 14.132999897003174
   729     1.235872e+01     8.549679e-01
 * time: 14.161999940872192
   730     1.235865e+01     8.541860e-01
 * time: 14.168999910354614
   731     1.235858e+01     8.549660e-01
 * time: 14.186000108718872
   732     1.235851e+01     8.541853e-01
 * time: 14.206000089645386
   733     1.235843e+01     8.549640e-01
 * time: 14.223000049591064
   734     1.235836e+01     8.541846e-01
 * time: 14.256999969482422
   735     1.235829e+01     8.549620e-01
 * time: 14.282999992370605
   736     1.235822e+01     8.5418

   842     1.235053e+01     8.541473e-01
 * time: 16.588000059127808
   843     1.235045e+01     8.548569e-01
 * time: 16.59500002861023
   844     1.235038e+01     8.541466e-01
 * time: 16.61400008201599
   845     1.235031e+01     8.548550e-01
 * time: 16.621000051498413
   846     1.235024e+01     8.541459e-01
 * time: 16.628000020980835
   847     1.235016e+01     8.548530e-01
 * time: 16.632999897003174
   848     1.235009e+01     8.541452e-01
 * time: 16.66599988937378
   849     1.235002e+01     8.548511e-01
 * time: 16.691999912261963
   850     1.234995e+01     8.541445e-01
 * time: 16.710000038146973
   851     1.234987e+01     8.548492e-01
 * time: 16.717000007629395
   852     1.234980e+01     8.541438e-01
 * time: 16.73300004005432
   853     1.234973e+01     8.548472e-01
 * time: 16.763000011444092
   854     1.234966e+01     8.541431e-01
 * time: 16.793999910354614
   855     1.234958e+01     8.548453e-01
 * time: 16.79800009727478
   856     1.234951e+01     8.541424e-0

   962     1.234182e+01     8.541055e-01
 * time: 18.89299988746643
   963     1.234175e+01     8.547420e-01
 * time: 18.907999992370605
   964     1.234167e+01     8.541048e-01
 * time: 18.913000106811523
   965     1.234160e+01     8.547401e-01
 * time: 18.92799997329712
   966     1.234153e+01     8.541041e-01
 * time: 18.93499994277954
   967     1.234146e+01     8.547382e-01
 * time: 18.95799994468689
   968     1.234138e+01     8.541034e-01
 * time: 18.996000051498413
   969     1.234131e+01     8.547363e-01
 * time: 19.02900004386902
   970     1.234124e+01     8.541027e-01
 * time: 19.033999919891357
   971     1.234117e+01     8.547344e-01
 * time: 19.075999975204468
   972     1.234109e+01     8.541020e-01
 * time: 19.085000038146973
   973     1.234102e+01     8.547325e-01
 * time: 19.09599995613098
   974     1.234095e+01     8.541013e-01
 * time: 19.125
   975     1.234087e+01     8.547306e-01
 * time: 19.1489999294281
   976     1.234080e+01     8.541006e-01
 * time: 19.1

 * Status: failure (reached maximum number of iterations) (line search failed)

 * Candidate solution
    Minimizer: [4.51e+00, 2.04e+01]
    Minimum:   1.233906e+01

 * Found with
    Algorithm:     Gradient Descent
    Initial Point: [2.00e+01, 2.00e+01]

 * Convergence measures
    |x - x'|               = 1.04e-04 ≰ 0.0e+00
    |x - x'|/|x'|          = 5.09e-06 ≰ 0.0e+00
    |f(x) - f(x')|         = 7.26e-05 ≰ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 5.88e-06 ≰ 0.0e+00
    |g(x)|                 = 8.54e-01 ≰ 1.0e-06

 * Work counters
    Seconds run:   20  (vs limit Inf)
    Iterations:    1000
    f(x) calls:    2506
    ∇f(x) calls:   2506


In [10]:
res = optimize(rosenbrock, rosenbrock_gradient!,
               [20.0, 20.0],
               Optim.BFGS(),
               Optim.Options(g_tol = 1e-6,
                             store_trace = true,
                             show_trace = true))

Iter     Function value   Gradient norm 
     0     1.444036e+07     3.040038e+06
 * time: 0.0
     1     2.680958e+06     8.881503e+05
 * time: 0.014999866485595703
     2     6.650571e+05     5.858550e+05
 * time: 0.01699995994567871
     3     2.806304e+02     7.167345e+02
 * time: 0.03399991989135742
     4     2.794972e+02     3.772877e+01
 * time: 0.04799985885620117
     5     2.694629e+02     8.824642e+02
 * time: 0.06099987030029297
     6     2.679257e+02     1.073784e+03
 * time: 0.07499980926513672
     7     2.615432e+02     1.595776e+03
 * time: 0.11699986457824707
     8     2.480323e+02     1.178047e+03
 * time: 0.12099981307983398
     9     2.411404e+02     6.281265e+02
 * time: 0.12599992752075195
    10     2.318473e+02     2.328093e+02
 * time: 0.14699983596801758
    11     2.293179e+02     7.429504e+02
 * time: 0.18599987030029297
    12     2.271862e+02     1.282135e+03
 * time: 0.20199990272521973
    13     2.195866e+02     1.511525e+03
 * time: 0.208999872207

 * Status: success

 * Candidate solution
    Minimizer: [1.00e+00, 1.00e+00]
    Minimum:   8.109975e-17

 * Found with
    Algorithm:     BFGS
    Initial Point: [2.00e+01, 2.00e+01]

 * Convergence measures
    |x - x'|               = 9.19e-06 ≰ 0.0e+00
    |x - x'|/|x'|          = 9.19e-06 ≰ 0.0e+00
    |f(x) - f(x')|         = 2.55e-11 ≰ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 3.15e+05 ≰ 0.0e+00
    |g(x)|                 = 3.27e-07 ≤ 1.0e-06

 * Work counters
    Seconds run:   2  (vs limit Inf)
    Iterations:    95
    f(x) calls:    284
    ∇f(x) calls:   284


In [11]:
using BenchmarkTools

@btime res = optimize(rosenbrock, rosenbrock_gradient!,
                   [0.0, 0.0], Optim.BFGS(),
               Optim.Options(g_tol = 1e-6,
                             store_trace = true,
                             show_trace = false))

  36.800 μs (558 allocations: 29.64 KiB)


 * Status: success

 * Candidate solution
    Minimizer: [1.00e+00, 1.00e+00]
    Minimum:   7.645563e-21

 * Found with
    Algorithm:     BFGS
    Initial Point: [0.00e+00, 0.00e+00]

 * Convergence measures
    |x - x'|               = 3.48e-07 ≰ 0.0e+00
    |x - x'|/|x'|          = 3.48e-07 ≰ 0.0e+00
    |f(x) - f(x')|         = 6.91e-14 ≰ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 9.03e+06 ≰ 0.0e+00
    |g(x)|                 = 2.32e-09 ≤ 1.0e-06

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    16
    f(x) calls:    53
    ∇f(x) calls:   53


In [12]:
iter = Optim.trace(res)

96-element Array{OptimizationState{Float64,BFGS{LineSearches.InitialStatic{Float64},LineSearches.HagerZhang{Float64,Base.RefValue{Bool}},Nothing,Nothing,Flat}},1}:
      0     1.444036e+07     3.040038e+06
 * time: 0.0
                 
      1     2.680958e+06     8.881503e+05
 * time: 0.014999866485595703

      2     6.650571e+05     5.858550e+05
 * time: 0.01699995994567871
 
      3     2.806304e+02     7.167345e+02
 * time: 0.03399991989135742
 
      4     2.794972e+02     3.772877e+01
 * time: 0.04799985885620117
 
      5     2.694629e+02     8.824642e+02
 * time: 0.06099987030029297
 
      6     2.679257e+02     1.073784e+03
 * time: 0.07499980926513672
 
      7     2.615432e+02     1.595776e+03
 * time: 0.11699986457824707
 
      8     2.480323e+02     1.178047e+03
 * time: 0.12099981307983398
 
      9     2.411404e+02     6.281265e+02
 * time: 0.12599992752075195
 
     10     2.318473e+02     2.328093e+02
 * time: 0.14699983596801758
 
     11     2.293179e+02     7.42

## Differentiation in Julia

Computing gradient and Hessian of complicated, and even sometimes simple, functions can be tedious. In order to alleviate this burden, it is possible to use numerical derivates or automatic differentiation.

### Numerical derivatives

Numerical derivatives function are provided in the package Calculus, as illustrated below.

In [13]:
using Calculus, LinearAlgebra
rg = Calculus.gradient(rosenbrock)

#2 (generic function with 1 method)

Let's evaluate the newly constructed gradient function at the solution [1,1].

In [14]:
gsol = rg([1,1])

2-element Array{Float64,1}:
  1.4667356107373247e-8 
 -1.1102239280930583e-14

We are close to zero, but there are approximation errors, that can prevent the convergence to the right solution, or at least impact the solution accuracy, as

In [15]:
norm(gsol)

1.466735610737745e-8

In [16]:
storage = [0.0,0.0]
function rg!(storage::Vector, x::Vector)
    s = rg(x)
    storage[1:length(s)] = s[1:length(s)]
end

rg! (generic function with 1 method)

In [17]:
storage

2-element Array{Float64,1}:
 0.0
 0.0

In [18]:
@btime res = optimize(rosenbrock, rg!,
               [0.0, 0.0],
               Optim.BFGS(),
               Optim.Options(g_tol = 1e-12,
                             store_trace = true,
                             show_trace = false))

  62.899 μs (803 allocations: 44.81 KiB)


 * Status: success

 * Candidate solution
    Minimizer: [1.00e+00, 1.00e+00]
    Minimum:   5.378308e-17

 * Found with
    Algorithm:     BFGS
    Initial Point: [0.00e+00, 0.00e+00]

 * Convergence measures
    |x - x'|               = 1.32e-10 ≰ 0.0e+00
    |x - x'|/|x'|          = 1.32e-10 ≰ 0.0e+00
    |f(x) - f(x')|         = 9.31e-19 ≰ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 1.73e-02 ≰ 0.0e+00
    |g(x)|                 = 2.78e-13 ≤ 1.0e-12

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    17
    f(x) calls:    55
    ∇f(x) calls:   55


In [22]:
res = optimize(rosenbrock, rg!,
               [1.1, 1.1],
               Optim.GradientDescent(),
               Optim.Options(g_tol = 1e-12,
                             store_trace = true,
                             show_trace = true))

Iter     Function value   Gradient norm 
     0     1.220000e+00     4.860000e+01
 * time: 0.0009999275207519531
     1     5.804214e-03     2.125407e+00
 * time: 0.03600001335144043
     2     3.342431e-03     4.583199e-02
 * time: 0.0409998893737793
     3     3.025234e-03     7.072574e-01
 * time: 0.06200003623962402
     4     2.774066e-03     1.561595e-01
 * time: 0.10399985313415527
     5     2.754813e-03     3.619916e-02
 * time: 0.1099998950958252
     6     2.735659e-03     1.553929e-01
 * time: 0.1419999599456787
     7     2.716594e-03     3.619630e-02
 * time: 0.1549999713897705
     8     2.695676e-03     1.642356e-01
 * time: 0.18599987030029297
     9     2.674873e-03     3.622467e-02
 * time: 0.20799994468688965
    10     2.651249e-03     1.769096e-01
 * time: 0.21499991416931152
    11     2.627785e-03     3.631260e-02
 * time: 0.24199986457824707
    12     2.599317e-03     1.979975e-01
 * time: 0.2739999294281006
    13     2.571002e-03     3.655250e-02
 * time: 0.

   119     1.880020e-03     5.413229e-02
 * time: 2.8910000324249268
   120     1.877264e-03     4.293461e-02
 * time: 2.8980000019073486
   121     1.874512e-03     5.406321e-02
 * time: 2.927999973297119
   122     1.871763e-03     4.286507e-02
 * time: 2.947999954223633
   123     1.869018e-03     5.399418e-02
 * time: 2.99399995803833
   124     1.866276e-03     4.279563e-02
 * time: 3.010999917984009
   125     1.863538e-03     5.392520e-02
 * time: 3.0199999809265137
   126     1.860803e-03     4.272629e-02
 * time: 3.0239999294281006
   127     1.858073e-03     5.385628e-02
 * time: 3.0320000648498535
   128     1.855345e-03     4.265704e-02
 * time: 3.059000015258789
   129     1.852621e-03     5.378742e-02
 * time: 3.072999954223633
   130     1.849901e-03     4.258788e-02
 * time: 3.1019999980926514
   131     1.847184e-03     5.371860e-02
 * time: 3.119999885559082
   132     1.844470e-03     4.251883e-02
 * time: 3.138000011444092
   133     1.841761e-03     5.364985e-02
 *

   240     1.571295e-03     3.892857e-02
 * time: 5.138999938964844
   241     1.568943e-03     5.001681e-02
 * time: 5.1570000648498535
   242     1.566593e-03     3.886461e-02
 * time: 5.16700005531311
   243     1.564247e-03     4.995101e-02
 * time: 5.181999921798706
   244     1.561903e-03     3.880075e-02
 * time: 5.187000036239624
   245     1.559563e-03     4.988527e-02
 * time: 5.191999912261963
   246     1.557226e-03     3.873697e-02
 * time: 5.2170000076293945
   247     1.554892e-03     4.981958e-02
 * time: 5.241999864578247
   248     1.552561e-03     3.867328e-02
 * time: 5.253999948501587
   249     1.550234e-03     4.975395e-02
 * time: 5.2829999923706055
   250     1.547909e-03     3.860968e-02
 * time: 5.299999952316284
   251     1.545588e-03     4.968837e-02
 * time: 5.32099986076355
   252     1.543269e-03     3.854617e-02
 * time: 5.348999977111816
   253     1.540954e-03     4.962285e-02
 * time: 5.352999925613403
   254     1.538641e-03     3.848275e-02
 * tim

   361     1.308283e-03     4.616488e-02
 * time: 7.510999917984009
   362     1.306283e-03     3.518888e-02
 * time: 7.523999929428101
   363     1.304286e-03     4.610234e-02
 * time: 7.537999868392944
   364     1.302292e-03     3.513025e-02
 * time: 7.559000015258789
   365     1.300300e-03     4.603985e-02
 * time: 7.572000026702881
   366     1.298311e-03     3.507172e-02
 * time: 7.575000047683716
   367     1.296325e-03     4.597742e-02
 * time: 7.58899998664856
   368     1.294342e-03     3.501326e-02
 * time: 7.605999946594238
   369     1.292361e-03     4.591504e-02
 * time: 7.621000051498413
   370     1.290383e-03     3.495489e-02
 * time: 7.63700008392334
   371     1.288407e-03     4.585271e-02
 * time: 7.651000022888184
   372     1.286435e-03     3.489661e-02
 * time: 7.670000076293945
   373     1.284465e-03     4.579044e-02
 * time: 7.684999942779541
   374     1.282497e-03     3.483841e-02
 * time: 7.703000068664551
   375     1.280533e-03     4.572822e-02
 * time: 

   482     1.085188e-03     3.181818e-02
 * time: 9.973999977111816
   483     1.083495e-03     4.244946e-02
 * time: 9.993000030517578
   484     1.081805e-03     3.176448e-02
 * time: 10.02999997138977
   485     1.080118e-03     4.239024e-02
 * time: 10.045000076293945
   486     1.078432e-03     3.171085e-02
 * time: 10.066999912261963
   487     1.076749e-03     4.233108e-02
 * time: 10.075999975204468
   488     1.075069e-03     3.165730e-02
 * time: 10.098000049591064
   489     1.073391e-03     4.227197e-02
 * time: 10.102999925613403
   490     1.071715e-03     3.160383e-02
 * time: 10.14299988746643
   491     1.070041e-03     4.221292e-02
 * time: 10.157000064849854
   492     1.068370e-03     3.155044e-02
 * time: 10.174999952316284
   493     1.066701e-03     4.215393e-02
 * time: 10.180000066757202
   494     1.065034e-03     3.149713e-02
 * time: 10.188999891281128
   495     1.063370e-03     4.209498e-02
 * time: 10.210999965667725
   496     1.061708e-03     3.144390e-

   601     8.996462e-04     3.904949e-02
 * time: 12.476999998092651
   602     8.982162e-04     2.873293e-02
 * time: 12.494999885559082
   603     8.967883e-04     3.899351e-02
 * time: 12.5
   604     8.953624e-04     2.868382e-02
 * time: 12.516000032424927
   605     8.939386e-04     3.893759e-02
 * time: 12.520999908447266
   606     8.925167e-04     2.863478e-02
 * time: 12.527999877929688
   607     8.910970e-04     3.888171e-02
 * time: 12.535000085830688
   608     8.896792e-04     2.858582e-02
 * time: 12.549000024795532
   609     8.882636e-04     3.882590e-02
 * time: 12.55299997329712
   610     8.868499e-04     2.853693e-02
 * time: 12.578999996185303
   611     8.854383e-04     3.877014e-02
 * time: 12.598000049591064
   612     8.840286e-04     2.848811e-02
 * time: 12.631999969482422
   613     8.826211e-04     3.871443e-02
 * time: 12.648000001907349
   614     8.812155e-04     2.843937e-02
 * time: 12.654000043869019
   615     8.798120e-04     3.865878e-02
 * time:

   721     7.419969e-04     3.578773e-02
 * time: 14.810999870300293
   722     7.407956e-04     2.591399e-02
 * time: 14.82699990272522
   723     7.395962e-04     3.573504e-02
 * time: 14.842000007629395
   724     7.383984e-04     2.586916e-02
 * time: 14.846999883651733
   725     7.372024e-04     3.568240e-02
 * time: 14.875
   726     7.360081e-04     2.582440e-02
 * time: 14.894000053405762
   727     7.348157e-04     3.562982e-02
 * time: 14.912999868392944
   728     7.336250e-04     2.577970e-02
 * time: 14.917999982833862
   729     7.324360e-04     3.557730e-02
 * time: 14.937000036239624
   730     7.312488e-04     2.573508e-02
 * time: 14.960000038146973
   731     7.300634e-04     3.552483e-02
 * time: 14.983000040054321
   732     7.288796e-04     2.569052e-02
 * time: 15.023000001907349
   733     7.276977e-04     3.547241e-02
 * time: 15.059999942779541
   734     7.265174e-04     2.564603e-02
 * time: 15.079999923706055
   735     7.253389e-04     3.542005e-02
 * tim

   841     6.098403e-04     3.272303e-02
 * time: 17.027999877929688
   842     6.088356e-04     2.334287e-02
 * time: 17.055000066757202
   843     6.078324e-04     3.267361e-02
 * time: 17.060999870300293
   844     6.068306e-04     2.330201e-02
 * time: 17.06599998474121
   845     6.058304e-04     3.262425e-02
 * time: 17.092000007629395
   846     6.048317e-04     2.326122e-02
 * time: 17.096999883651733
   847     6.038345e-04     3.257494e-02
 * time: 17.10199999809265
   848     6.028388e-04     2.322050e-02
 * time: 17.11899995803833
   849     6.018446e-04     3.252569e-02
 * time: 17.14400005340576
   850     6.008519e-04     2.317983e-02
 * time: 17.191999912261963
   851     5.998607e-04     3.247649e-02
 * time: 17.264999866485596
   852     5.988710e-04     2.313923e-02
 * time: 17.280999898910522
   853     5.978828e-04     3.242735e-02
 * time: 17.295000076293945
   854     5.968960e-04     2.309870e-02
 * time: 17.316999912261963
   855     5.959108e-04     3.237825e-

 * time: 20.44099998474121
   961     4.995336e-04     2.985381e-02
 * time: 20.506999969482422
   962     4.986968e-04     2.100181e-02
 * time: 20.549000024795532
   963     4.978613e-04     2.980763e-02
 * time: 20.575000047683716
   964     4.970271e-04     2.096465e-02
 * time: 20.59999990463257
   965     4.961942e-04     2.976150e-02
 * time: 20.65400004386902
   966     4.953626e-04     2.092754e-02
 * time: 20.680999994277954
   967     4.945323e-04     2.971543e-02
 * time: 20.7189998626709
   968     4.937032e-04     2.089049e-02
 * time: 20.7739999294281
   969     4.928755e-04     2.966941e-02
 * time: 20.81599998474121
   970     4.920489e-04     2.085350e-02
 * time: 20.90499997138977
   971     4.912237e-04     2.962345e-02
 * time: 20.990000009536743
   972     4.903998e-04     2.081657e-02
 * time: 21.00499987602234
   973     4.895771e-04     2.957754e-02
 * time: 21.032000064849854
   974     4.887557e-04     2.077970e-02
 * time: 21.10199999809265
   975     4.8793

 * Status: failure (reached maximum number of iterations) (line search failed)

 * Candidate solution
    Minimizer: [1.02e+00, 1.04e+00]
    Minimum:   4.678395e-04

 * Found with
    Algorithm:     Gradient Descent
    Initial Point: [1.10e+00, 1.10e+00]

 * Convergence measures
    |x - x'|               = 4.17e-05 ≰ 0.0e+00
    |x - x'|/|x'|          = 3.99e-05 ≰ 0.0e+00
    |f(x) - f(x')|         = 7.89e-07 ≰ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 1.69e-03 ≰ 0.0e+00
    |g(x)|                 = 2.03e-02 ≰ 1.0e-12

 * Work counters
    Seconds run:   22  (vs limit Inf)
    Iterations:    1000
    f(x) calls:    2515
    ∇f(x) calls:   2515


### Automatic differentiation

In [23]:
using Pkg
Pkg.add("ForwardDiff")

  Updating registry at `C:\Users\slash\.julia\registries\General`
  Updating git-repo `https://github.com/JuliaRegistries/General.git`
Fetching: [========================================>]  100.0 %.0 %.6 %.9 % [=====>                                   ]  11.7 %2 %=========>                               ]  20.0 %==========>                              ]  23.3 %Fetching: [=============>                           ]  32.0 %Fetching: [================>                        ]  38.3 %42.3 % [==================>                      ]  44.9 %                   ]  51.3 %======================>                  ]  52.8 % %3 %0 %.5 %72.1 %Fetching: [==============================>          ]  73.9 %.0 %.6 %.2 %>        ]  78.1 % [================================>        ]  79.3 %Fetching: [====================================>    ]  88.4 % [=====================================>   ]  91.8 %>  ]  94.2 % [=======================================> ]  95.1 %]  97.9 % Resolving package versions...


In [24]:
using ForwardDiff

g = x -> ForwardDiff.gradient(rosenbrock, x);
H = x -> ForwardDiff.hessian(rosenbrock, x)

function g!(storage::Vector, x::Vector)
    s = g(x)
    storage[1:length(s)] = s[1:length(s)]
end

g! (generic function with 1 method)

In [25]:
g([1.0,1.0])

2-element Array{Float64,1}:
 -0.0
  0.0

In [26]:
res = optimize(rosenbrock, g!,
               [0.0, 0.0],
               Optim.BFGS(),
               Optim.Options(g_tol = 1e-6,
                             store_trace = true,
                             show_trace = false))

 * Status: success

 * Candidate solution
    Minimizer: [1.00e+00, 1.00e+00]
    Minimum:   7.645684e-21

 * Found with
    Algorithm:     BFGS
    Initial Point: [0.00e+00, 0.00e+00]

 * Convergence measures
    |x - x'|               = 3.48e-07 ≰ 0.0e+00
    |x - x'|/|x'|          = 3.48e-07 ≰ 0.0e+00
    |f(x) - f(x')|         = 6.91e-14 ≰ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 9.03e+06 ≰ 0.0e+00
    |g(x)|                 = 2.32e-09 ≤ 1.0e-06

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    16
    f(x) calls:    53
    ∇f(x) calls:   53


In [27]:
@btime res = optimize(rosenbrock, g!,
               [0.0, 0.0],
               Optim.BFGS(),
               Optim.Options(g_tol = 1e-6,
                             store_trace = true,
                             show_trace = false))

  79.900 μs (876 allocations: 52.00 KiB)


 * Status: success

 * Candidate solution
    Minimizer: [1.00e+00, 1.00e+00]
    Minimum:   7.645684e-21

 * Found with
    Algorithm:     BFGS
    Initial Point: [0.00e+00, 0.00e+00]

 * Convergence measures
    |x - x'|               = 3.48e-07 ≰ 0.0e+00
    |x - x'|/|x'|          = 3.48e-07 ≰ 0.0e+00
    |f(x) - f(x')|         = 6.91e-14 ≰ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 9.03e+06 ≰ 0.0e+00
    |g(x)|                 = 2.32e-09 ≤ 1.0e-06

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    16
    f(x) calls:    53
    ∇f(x) calls:   53


## Newton method

$$
x_{k+1} = x_k-\nabla^2 f(x_k)^{-1} \nabla f(x_k)
$$
or
$$
\nabla^2 f(x_k) x_{k+1} = \nabla^2 f(x_k) x_k- \nabla f(x_k)
$$


In [28]:
function Newton(f::Function, g::Function, h:: Function,
        xstart::Vector, verbose::Bool = false,
        δ::Float64 = 1e-6, nmax::Int64 = 1000)

    k = 1
    x = xstart
    n = length(x)
    δ2 = δ*δ
    H = zeros(n,n)+I
    dfx = ones(n)
    
    if (verbose)
        fx = f(x)
        println("$k. x = $x, f(x) = $fx")
    end

    g(dfx, x)

    while (dot(dfx,dfx) > δ2 && k <= nmax)
        k += 1
        g(dfx,x)
        h(H,x)
        # Hs = -dfx, x_{k+1} = x_k - s # s = -inv(H)*dfx vs s = -H\dfx
        x -= H\dfx  # x = x - s
        if (verbose)
            fx = f(x)
            println("$k. x = $x, f(x) = $fx ")
        end
    end
end

Newton (generic function with 4 methods)

In [29]:
Newton(rosenbrock, rosenbrock_gradient!, rosenbrock_hessian!, [-100.0,100.0], true)

1. x = [-100.0, 100.0], f(x) = 9.801010201e9
2. x = [-99.99994898992475, 9999.989797984948], f(x) = 10200.9896959674 
3. x = [0.9999473760899633, -10199.97917119076], f(x) = 1.0405997390386257e10 
4. x = [0.9999473761157568, 0.9998947549993318], f(x) = 2.7692731928427748e-9 
5. x = [0.9999999999999847, 0.9999999972306961], f(x) = 7.668874361715257e-16 
6. x = [1.0, 1.0], f(x) = 0.0 
7. x = [1.0, 1.0], f(x) = 0.0 


## Implementation of a linesearch algorithm

A very basic linesearch implementation skeleton follows.

In [38]:
function ls(f::Function, g::Function, h:: Function,
        x0::Vector,
        direction::Function, steplength::Function,
        δ::Float64 = 1e-6, nmax::Int64 = 1000)

    k = 0
    x = x0
    δ2 = δ*δ
    n = length(x)

    dfx = ones(n)

    g(dfx, x)

#    println("$k. $x")

    while (dot(dfx,dfx) > δ2 && k <= nmax)
        # Compute the search direction
        d, dfx = direction(f,g,h,x)
        # Compute the step length along d
        α = steplength(f,dfx,x,d)
        # Update the iterate
        x += α*d
        k += 1
#        println("$k. $x")
    end
    
    return x
end

ls (generic function with 3 methods)

In [39]:
constantStep(f::Function, dfx:: Vector, x:: Vector, d::Vector) = 1

constantStep (generic function with 1 method)

In [42]:
n = 3;
Matrix{Float64}(I,n,n)

3×3 Array{Float64,2}:
 1.0  0.0  0.0
 0.0  1.0  0.0
 0.0  0.0  1.0

In [41]:
function direction(f::Function, g:: Function, h:: Function, x::Vector)
    n = length(x)
    df = ones(n)
    H = zeros(n,n)+I
    g(df,x)
    h(H,x)
    return -H\df, df
end

direction (generic function with 1 method)

In [43]:
x = ls(rosenbrock, rosenbrock_gradient!, rosenbrock_hessian!,
       [0.0,0.0], direction, constantStep)

2-element Array{Float64,1}:
 1.0
 1.0

In [46]:
function ArmijoStep(f::Function, dfx::Vector, x::Vector, d:: Vector,
    αmax:: Float64 = 1.0, β:: Float64 =0.1, κ:: Float64 =0.2)
    
    s = β*dot(dfx,d)
    α = αmax
    
    fx = f(x)
    fxcand = f(x+α*d)
    
    while (fxcand >= fx+α*s)
        α *= κ
        fxcand = f(x+α*d)        
    end
    
    return α
end

ArmijoStep (generic function with 4 methods)

In [47]:
@btime x =ls(rosenbrock, rosenbrock_gradient!, rosenbrock_hessian!,
          [0.0,0.0], direction, ArmijoStep)

  18.599 μs (221 allocations: 18.58 KiB)


2-element Array{Float64,1}:
 0.9999999999999569
 0.9999999999998284

In [48]:
norm(ones(2)-x)

0.0

In [49]:
function direction3(f::Function, g:: Function, h:: Function, x::Vector)
    n = length(x)
    df = ones(n)
    H = zeros(n,n)+I
    g(df,x)
    h(H,x)
    H[1,2] = H[2,1]= 0.0
    return -H\df, df
end

direction3 (generic function with 1 method)

In [50]:
ls(rosenbrock, rosenbrock_gradient!, rosenbrock_hessian!,
    [0.0,0.0], direction3, ArmijoStep)

2-element Array{Float64,1}:
 0.9259531981936803
 0.8567279574660482